In [63]:
from copy import deepcopy

import note_seq
import numpy as np
import tensorflow.compat.v1 as tf
from magenta.models.score2perf import score2perf
from tensor2tensor import problems
from tensor2tensor.data_generators import text_encoder
from tensor2tensor.utils import decoding, trainer_lib

tf.disable_v2_behavior()

## Helper Functions and Constants

In [41]:
SF2_PATH = 'soundfonts/Yamaha-C5-Salamander-JNv5.1.sf2'
SAMPLE_RATE = float(44100)

In [42]:
def decode(ids, encoder):
    ids = list(ids)
    if text_encoder.EOS_ID in ids:
        ids = ids[:ids.index(text_encoder.EOS_ID)]
    return encoder.decode(ids)

In [43]:
def load_midi(midi_file_path):
    return note_seq.midi_file_to_note_sequence(midi_file_path)

## Unconditioned Model

In [44]:
ckpt_path = 'models/music_transformer/unconditional_model_16.ckpt'

In [45]:
class PianoPerformanceLanguageModelProblem(score2perf.Score2PerfProblem):
    @property
    def add_eos_symbol(self):
      return True

In [46]:
problem = PianoPerformanceLanguageModelProblem()

In [47]:
unconditional_encoders = problem.get_feature_encoders()

In [48]:
hparams = trainer_lib.create_hparams(hparams_set='transformer_tpu')
trainer_lib.add_problem_hparams(hparams, problem)
hparams.num_hidden_layers = 16
hparams.sampling_method = 'random'

In [49]:
decode_hparams = decoding.decode_hparams()
decode_hparams.alpha = 0.0
decode_hparams.beam_size = 1

In [ ]:
run_config = trainer_lib.create_run_config(hparams)
estimator = trainer_lib.create_estimator('transformer', hparams, run_config, decode_hparams=decode_hparams)

In [51]:
def input_generator():
    global targets
    global decode_length
    while True:
        print('yielding', len(targets))
        yield {
            'targets': np.array([targets], dtype=np.int32),
            'decode_length': np.array(decode_length, dtype=np.int32)
        }

In [52]:
targets = []
decode_length = 0

In [53]:
input_fn = decoding.make_input_fn_from_generator(input_generator())
unconditional_samples = estimator.predict(input_fn, checkpoint_path=ckpt_path)

yielding 0


In [ ]:
_ = next(unconditional_samples)

In [55]:
targets = []
decode_length = 1024

In [56]:
sample_ids = next(unconditional_samples)['outputs']

yielding 0


In [57]:
midi_filename = decode(sample_ids, encoder=unconditional_encoders['targets'])

In [58]:
unconditional_ns = note_seq.midi_file_to_note_sequence(midi_filename)

In [59]:
note_seq.play_sequence(unconditional_ns, synth=note_seq.fluidsynth, sample_rate=SAMPLE_RATE, sf2_path=SF2_PATH)
note_seq.plot_sequence(unconditional_ns)

Loading BokehJS ...

In [61]:
# save midi file
# import shutil
# shutil.copy(midi_filename, 'für_elise_output.mid')

'für_elise_output.mid'

In [62]:
# play midi file
note_seq.play_sequence(note_seq.midi_file_to_note_sequence('für_elise_output.mid'), synth=note_seq.fluidsynth, sample_rate=SAMPLE_RATE, sf2_path=SF2_PATH)

## Generate Continuation from priming sequence (seed melody)

In [ ]:
filenames = {
    'C major arpeggio': 'data/c_major_arpeggio.mid',
    'C major scale': 'data/c_major_scale.mid',
    'Clair de Lune': 'data/clair_de_lune.mid',
}

In [ ]:
primer = 'Clair de Lune'  

In [ ]:
primer_ns = note_seq.midi_file_to_note_sequence(filenames[primer])

In [ ]:
primer_ns = note_seq.apply_sustain_control_changes(primer_ns)

In [ ]:
max_primer_seconds = 20
if primer_ns.total_time > max_primer_seconds:
    print('Primer is longer than %d seconds, truncating.' % max_primer_seconds)
    primer_ns = note_seq.extract_subsequence(
        primer_ns, 0, max_primer_seconds)

In [ ]:
if any(note.is_drum for note in primer_ns.notes):
    print('Primer contains drums; they will be removed.')
    notes = [note for note in primer_ns.notes if not note.is_drum]
    del primer_ns.notes[:]
    primer_ns.notes.extend(notes)

In [ ]:
for note in primer_ns.notes:
  note.instrument = 1
  note.program = 0

In [ ]:
note_seq.play_sequence(primer_ns, synth=note_seq.fluidsynth, sample_rate=SAMPLE_RATE, sf2_path=SF2_PATH)
note_seq.plot_sequence(primer_ns)

In [ ]:
targets = unconditional_encoders['targets'].encode_note_sequence(primer_ns)

In [ ]:
targets = targets[:-1]

In [ ]:
decode_length = max(0, 4096 - len(targets))
if len(targets) >= 4096:
    print('Primer has more events than maximum sequence length; nothing will be generated.')

In [ ]:
sample_ids = next(unconditional_samples)['outputs']

In [ ]:
midi_filename = decode(sample_ids, encoder=unconditional_encoders['targets'])
ns = note_seq.midi_file_to_note_sequence(midi_filename)

In [ ]:
continuation_ns = note_seq.concatenate_sequences([primer_ns, ns])

In [ ]:
note_seq.play_sequence(continuation_ns, synth=note_seq.fluidsynth, sample_rate=SAMPLE_RATE, sf2_path=SF2_PATH)
note_seq.plot_sequence(continuation_ns)

## Score Conditioning

In [ ]:
ckpt_path = 'models/music_transformer/melody_conditioned_model_16.ckpt'

In [ ]:
class MelodyToPianoPerformanceProblem(score2perf.AbsoluteMelody2PerfProblem):
  @property
  def add_eos_symbol(self):
    return True

In [ ]:
problem = MelodyToPianoPerformanceProblem()
melody_conditioned_encoders = problem.get_feature_encoders()

In [ ]:
hparams = trainer_lib.create_hparams(hparams_set='transformer_tpu')
trainer_lib.add_problem_hparams(hparams, problem)
hparams.num_hidden_layers = 16
hparams.sampling_method = 'random'

In [ ]:
run_config = trainer_lib.create_run_config(hparams)
estimator = trainer_lib.create_estimator(
    'transformer', hparams, run_config,
    decode_hparams=decode_hparams)

In [ ]:
inputs = []
decode_length = 0

In [ ]:
def input_generator():
  global inputs
  while True:
    yield {
        'inputs': np.array([[inputs]], dtype=np.int32),
        'targets': np.zeros([1, 0], dtype=np.int32),
        'decode_length': np.array(decode_length, dtype=np.int32)
    }

In [ ]:
input_fn = decoding.make_input_fn_from_generator(input_generator())
melody_conditioned_samples = estimator.predict(input_fn, checkpoint_path=ckpt_path)

In [ ]:
_ = next(melody_conditioned_samples)

## Choose Melody

In [ ]:
event_padding = 2 * [note_seq.MELODY_NO_EVENT]

In [ ]:
melodies = {
    'Mary Had a Little Lamb': [
        64, 62, 60, 62, 64, 64, 64, note_seq.MELODY_NO_EVENT,
        62, 62, 62, note_seq.MELODY_NO_EVENT,
        64, 67, 67, note_seq.MELODY_NO_EVENT,
        64, 62, 60, 62, 64, 64, 64, 64,
        62, 62, 64, 62, 60, note_seq.MELODY_NO_EVENT,
        note_seq.MELODY_NO_EVENT, note_seq.MELODY_NO_EVENT
    ],
    'Row Row Row Your Boat': [
        60, note_seq.MELODY_NO_EVENT, note_seq.MELODY_NO_EVENT,
        60, note_seq.MELODY_NO_EVENT, note_seq.MELODY_NO_EVENT,
        60, note_seq.MELODY_NO_EVENT, 62,
        64, note_seq.MELODY_NO_EVENT, note_seq.MELODY_NO_EVENT,
        64, note_seq.MELODY_NO_EVENT, 62,
        64, note_seq.MELODY_NO_EVENT, 65,
        67, note_seq.MELODY_NO_EVENT, note_seq.MELODY_NO_EVENT,
        note_seq.MELODY_NO_EVENT, note_seq.MELODY_NO_EVENT, note_seq.MELODY_NO_EVENT,
        72, 72, 72, 67, 67, 67, 64, 64, 64, 60, 60, 60,
        67, note_seq.MELODY_NO_EVENT, 65,
        64, note_seq.MELODY_NO_EVENT, 62,
        60, note_seq.MELODY_NO_EVENT, note_seq.MELODY_NO_EVENT,
        note_seq.MELODY_NO_EVENT, note_seq.MELODY_NO_EVENT, note_seq.MELODY_NO_EVENT
    ],
    'Twinkle Twinkle Little Star': [
        60, 60, 67, 67, 69, 69, 67, note_seq.MELODY_NO_EVENT,
        65, 65, 64, 64, 62, 62, 60, note_seq.MELODY_NO_EVENT,
        67, 67, 65, 65, 64, 64, 62, note_seq.MELODY_NO_EVENT,
        67, 67, 65, 65, 64, 64, 62, note_seq.MELODY_NO_EVENT,
        60, 60, 67, 67, 69, 69, 67, note_seq.MELODY_NO_EVENT,
        65, 65, 64, 64, 62, 62, 60, note_seq.MELODY_NO_EVENT        
    ]
}

In [ ]:
melody = 'data/spiegel.midi'

In [ ]:
# Extract melody from user-uploaded MIDI file.
melody_ns = load_midi(melody)
melody_instrument = note_seq.infer_melody_for_sequence(melody_ns)
notes = [note for note in melody_ns.notes if note.instrument == melody_instrument]
del melody_ns.notes[:]
melody_ns.notes.extend(sorted(notes, key=lambda note: note.start_time))

for i in range(len(melody_ns.notes) - 1):
  melody_ns.notes[i].end_time = melody_ns.notes[i + 1].start_time

inputs = melody_conditioned_encoders['inputs'].encode_note_sequence(melody_ns)

In [ ]:
# Use one of the provided melodies.
events = [event + 12 if event != note_seq.MELODY_NO_EVENT else event
          for e in melodies[melody]
          for event in [e] + event_padding]

inputs = melody_conditioned_encoders['inputs'].encode(' '.join(str(e) for e in events))
melody_ns = note_seq.Melody(events).to_sequence(qpm=150)

In [ ]:
note_seq.play_sequence(melody_ns, synth=note_seq.fluidsynth, sample_rate=SAMPLE_RATE, sf2_path=SF2_PATH)
note_seq.plot_sequence(melody_ns)

In [ ]:
decode_length = 4096
sample_ids = next(melody_conditioned_samples)['outputs']

In [ ]:
midi_filename = decode(sample_ids, encoder=melody_conditioned_encoders['targets'])
accompaniment_ns = note_seq.midi_file_to_note_sequence(midi_filename)

In [ ]:
note_seq.play_sequence(accompaniment_ns, synth=note_seq.fluidsynth, sample_rate=SAMPLE_RATE, sf2_path=SF2_PATH)
note_seq.plot_sequence(accompaniment_ns)

## Send Generated Sequence via OSC

In [ ]:
avril_ns = load_midi('data/henry-avril_14th.midi')
avril_ns = note_seq.apply_sustain_control_changes(avril_ns)

In [ ]:
avril_ns_copy = deepcopy(avril_ns)
avril_ns_copy = note_seq.quantize_note_sequence(avril_ns_copy, steps_per_quarter=4)

In [ ]:
note_seq.play_sequence(avril_ns, synth=note_seq.fluidsynth, sample_rate=SAMPLE_RATE, sf2_path=SF2_PATH)
note_seq.plot_sequence(avril_ns)

In [ ]:
avril_melody_instrument = note_seq.infer_melody_for_sequence(avril_ns)

In [ ]:
notes = [note for note in avril_ns.notes if note.instrument == avril_melody_instrument]
del avril_ns.notes[:]
avril_ns.notes.extend(sorted(notes, key=lambda note: note.start_time))
 
for i in range(len(avril_ns.notes) - 1):
    avril_ns.notes[i].end_time = avril_ns.notes[i + 1].start_time

In [ ]:
note_seq.play_sequence(avril_ns, synth=note_seq.fluidsynth, sample_rate=SAMPLE_RATE, sf2_path=SF2_PATH)
note_seq.plot_sequence(avril_ns)

In [ ]:
inputs = melody_conditioned_encoders['inputs'].encode_note_sequence(avril_ns)

In [ ]:
decode_length = 4096
sample_ids = next(melody_conditioned_samples)['outputs']

In [ ]:
midi_filename = decode(sample_ids, encoder=melody_conditioned_encoders['targets'])
avril_accompaniment_ns = note_seq.midi_file_to_note_sequence(midi_filename)

In [ ]:
note_seq.play_sequence(avril_accompaniment_ns, synth=note_seq.fluidsynth, sample_rate=SAMPLE_RATE, sf2_path=SF2_PATH)
note_seq.plot_sequence(avril_accompaniment_ns)